# Example

In [1]:
import os
import sys
import torch
import numpy as np
import soundfile as sf
from IPython.display import Audio

sys.path.append(
    os.path.abspath(
        os.path.join(
            os.path.dirname(os.path.realpath("file")), os.pardir, os.pardir, "ChatTTS"
        )
    )
)
import ChatTTS

torch._dynamo.config.cache_size_limit = 64  # type: ignore
torch._dynamo.config.suppress_errors = True  # type: ignore
torch.set_float32_matmul_precision("high")

## Load Models

In [ ]:
chat = ChatTTS.Chat()
chat.load_models(source="local", local_path="chattts/resources/nosft")

## Inference

### Batch infer

In [ ]:
texts = [
    "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with.",
] + [
    "我觉得像我们这些写程序的人，他，我觉得多多少少可能会对开源有一种情怀在吧我觉得开源是一个很好的形式。现在其实最先进的技术掌握在一些公司的手里的话，就他们并不会轻易的开放给所有的人用。"
]

wavs = chat.infer(texts)

In [41]:
Audio(wavs[0], rate=24_000, autoplay=True)

In [42]:
Audio(wavs[1], rate=24_000, autoplay=True)

### Custom params

In [46]:
text = "四川美食可多了，有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片等，每样都让人垂涎三尺。"
params_refine_text = {"prompt": "[oral_2][laugh_0][break_6]"}
params_infer_code = {"prompt": "[speed_5]", "temperature": 0.3}

wav = chat.infer(
    text=text,
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)

INFO:ChatTTS.core:All initialized.
 20%|█▉        | 400/2048 [00:21<01:26, 18.98it/s] 
/home/wanghao/code/Python/FunnyProject/.venv_chattts/lib/python3.10/site-packages/torch/nn/modules/conv.py:306: UserWarning: Plan failed with a cudnnException: CUDNN_BACKEND_EXECUTION_PLAN_DESCRIPTOR: cudnnFinalize Descriptor Failed cudnn_status: CUDNN_STATUS_NOT_SUPPORTED (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:919.)
  return F.conv1d(input, weight, bias, self.stride,


In [53]:
Audio(wav[0], rate=24_000, autoplay=True)

### fix random speaker

In [61]:
text = "四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃的口味温和，甜而不腻，也很受欢迎。"
params_refine_text = {"prompt": "[oral_2][laugh_0][break_6]"}
params_infer_code = {
    "spk_emb": chat.sample_random_speaker(),
    "temperature": 0.3,
    "top_P": 0.7,
    "top_K": 20,
}

wav = chat.infer(
    text=text,
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)

INFO:ChatTTS.core:All initialized.
 28%|██▊       | 569/2048 [00:04<00:12, 121.28it/s]


In [62]:
Audio(wav[0], rate=24_000, autoplay=True)

### Two stage control

In [37]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
text = chat.infer(text, refine_text_only=True)
wav = chat.infer(text, skip_refine_text=True)

INFO:ChatTTS.core:All initialized.
 21%|██        | 80/384 [00:00<00:02, 102.14it/s]
INFO:ChatTTS.core:All initialized.
 33%|███▎      | 684/2048 [00:06<00:13, 99.74it/s] 


In [36]:
display(text)
Audio(wav[0], rate=24_000, autoplay=True)

['so [uv_break] we found being competitive and collaborative was a huge way [uv_break] of staying motivated towards our goals, [uv_break] so [uv_break] one person to call when you fall off, [uv_break] one person who gets you back on then one person [uv_break] to actually do the activity with.']

## Summary

In [82]:
text = "鸡哥，人家真的很想骂你，可恶呀。"
text = chat.infer(text, refine_text_only=True)
display(text)

spk_emb = torch.as_tensor(
    data=np.load("women_speaker_latent.npy"), dtype=torch.float32, device="cuda:0"
)
params_refine_text = {"prompt": "[oral_2][laugh_0][break_6]"}
params_infer_code = {
    "spk_emb": spk_emb,
    "temperature": 0.3,
    "top_P": 0.7,
    "top_K": 20,
}
wav = chat.infer(
    text,
    skip_refine_text=True,
    params_refine_text=params_refine_text,
    params_infer_code=params_infer_code,
)
sf.write("example.wav", wavs[0].transpose(1, 0), 24_000)
Audio(wav[0], rate=24_000, autoplay=True)

INFO:ChatTTS.core:All initialized.
  6%|▌         | 23/384 [00:00<00:05, 72.19it/s]


['鸡 哥 ， 人 家 真 的 很 想 骂 你 啊 [uv_break] ， [laugh] 可 恶 呀 [uv_break] 。']

INFO:ChatTTS.core:All initialized.
  9%|▉         | 188/2048 [00:01<00:15, 121.30it/s]
